In [2]:
import tensorflow.compat.v1 as tf
tf.disable_v2_behavior()
import numpy as np
import matplotlib.pyplot as plt

Instructions for updating:
non-resource variables are not supported in the long term


In [3]:
#MInst 데이터 다운!! 
from tensorflow.examples.tutorials.mnist import input_data
mnist = input_data.read_data_sets("MNIST_data/", one_hot=True)

Instructions for updating:
Please use alternatives such as: tensorflow_datasets.load('mnist')
Instructions for updating:
Please write your own downloading logic.
Instructions for updating:
Please use tf.data to implement this functionality.
Extracting MNIST_data/train-images-idx3-ubyte.gz
Instructions for updating:
Please use tf.data to implement this functionality.
Extracting MNIST_data/train-labels-idx1-ubyte.gz
Instructions for updating:
Please use tf.one_hot on tensors.
Extracting MNIST_data/t10k-images-idx3-ubyte.gz
Extracting MNIST_data/t10k-labels-idx1-ubyte.gz
Instructions for updating:
Please use alternatives such as official/mnist/_DataSet.py from tensorflow/models.


In [4]:
#변수 선언
learning_rate_RMSProp = 0.02
learning_rate_GradientDescent = 0.5
num_epochs = 100
batch_size = 256
input_size = 784
hidden1_size = 128
hidden2_size = 64
display_step = 1

In [5]:
x = tf.placeholder(tf.float32 , shape=[None , input_size])
y = tf.placeholder(tf.float32 , shape=[None,10])

In [6]:
def build_autoencoder(x):
    #인코딩
    Wh1 = tf.Variable(tf.random_normal(shape=[input_size,hidden1_size]))
    bh1 = tf.Variable(tf.random_normal(shape=[hidden1_size]))
    H1_output = tf.nn.sigmoid(tf.matmul(x,Wh1)+bh1)
    Wh2 = tf.Variable(tf.random_normal(shape=[hidden1_size,hidden2_size]))
    bh2 = tf.Variable(tf.random_normal(shape=[hidden2_size]))
    H2_output = tf.nn.sigmoid(tf.matmul(H1_output,Wh2)+bh2)
    #디코딩
    Wh3 = tf.Variable(tf.random_normal(shape=[hidden2_size,hidden1_size]))
    bh3 = tf.Variable(tf.random_normal(shape=[hidden1_size]))
    H3_output = tf.nn.sigmoid(tf.matmul(H2_output,Wh3)+bh3)
    Wo = tf.Variable(tf.random_normal(shape=[hidden1_size,input_size]))
    bo = tf.Variable(tf.random_normal(shape=[input_size]))
    x_reconstructed = tf.nn.sigmoid(tf.matmul(H3_output,Wo)+bo)
    return x_reconstructed,H2_output

In [7]:
def build_softmax_classifier(x):
    W_softmax = tf.Variable(tf.zeros([hidden2_size,10]))
    b_softmax = tf.Variable(tf.zeros([10]))
    y_pred = tf.nn.softmax(tf.matmul(x,W_softmax)+b_softmax)
    return y_pred

In [8]:
y_pred , extracted_features = build_autoencoder(x)
y_true = x
y_pred_softmax = build_softmax_classifier(extracted_features)

In [9]:
pretraining_cost = tf.reduce_mean(tf.pow(y_true - y_pred,2))
pretraining_train_step = tf.train.RMSPropOptimizer(learning_rate_GradientDescent).minimize(pretraining_cost)
finetuning_cost = tf.reduce_mean(-tf.reduce_sum(y*tf.log(y_pred_softmax),reduction_indices=[1]))
finetuning_train_step = tf.train.GradientDescentOptimizer(learning_rate_GradientDescent).minimize(pretraining_cost)

Instructions for updating:
Call initializer instance with the dtype argument instead of passing it to the constructor


In [ ]:
with tf.Session() as sess:
    sess.run(tf.global_variables_initializer())
    total_batch = int(mnist.train.num_examples/batch_size)
    for step in range(num_epochs):
        for i in range(total_batch):
            batch_xs , batch_ys = mnist.train.next_batch(batch_size)
            _,pretraining_loss_print = sess.run([pretraining_train_step,pretraining_cost],feed_dict={x:batch_xs})
            if step % display_step == 0:
                print("반복(step) : %d ,pre-Training 손실함수(cost) : %f"%((step+1),pretraining_loss_print))
                print("Step1 : Mnist 데이터 재구축을 위한 오토인코거 최적화 완료!!")
    for step in range(num_epochs+10):
        for i in range(total_batch):
            batch_xs , batch_ys = mnist.train.next_batch(batch_size)
            _,finetuning_loss_print = sess.run([finetuning_train_step,finetuning_cost],feed_dict={x:batch_xs,y:batch_ys})
            if step % display_step == 0:
                print("반복(step) : %d ,pre-Training 손실함수(cost) : %f"%((step+1),finetuning_loss_print))
                print("Step2 : Mnist 데이터 재구축을 위한 오토인코거 최적화 완료 + softmax 분류기 최적화 완료(Fine Tuning)!!")

    correct_prediction = tf.equal(tf.argmax(y,1),tf.argmax(y_pred_softmax,1))
    accuracy = tf.reduce_mean(tf.cast(correct_prediction,tf.float32))
    print("정확도(오토인코거 + Softmax 분류기): %f"%sess.run(accuracy,feed_dict={x:mnist.test.images,y:mnist.test.labels}))

반복(step) : 1 ,pre-Training 손실함수(cost) : 0.423485
Step1 : Mnist 데이터 재구축을 위한 오토인코거 최적화 완료!!
반복(step) : 1 ,pre-Training 손실함수(cost) : 0.422976
Step1 : Mnist 데이터 재구축을 위한 오토인코거 최적화 완료!!
반복(step) : 1 ,pre-Training 손실함수(cost) : 0.422513
Step1 : Mnist 데이터 재구축을 위한 오토인코거 최적화 완료!!
반복(step) : 1 ,pre-Training 손실함수(cost) : 0.422330
Step1 : Mnist 데이터 재구축을 위한 오토인코거 최적화 완료!!
반복(step) : 1 ,pre-Training 손실함수(cost) : 0.421943
Step1 : Mnist 데이터 재구축을 위한 오토인코거 최적화 완료!!
반복(step) : 1 ,pre-Training 손실함수(cost) : 0.421521
Step1 : Mnist 데이터 재구축을 위한 오토인코거 최적화 완료!!
반복(step) : 1 ,pre-Training 손실함수(cost) : 0.422181
Step1 : Mnist 데이터 재구축을 위한 오토인코거 최적화 완료!!
반복(step) : 1 ,pre-Training 손실함수(cost) : 0.421484
Step1 : Mnist 데이터 재구축을 위한 오토인코거 최적화 완료!!
반복(step) : 1 ,pre-Training 손실함수(cost) : 0.420521
Step1 : Mnist 데이터 재구축을 위한 오토인코거 최적화 완료!!
반복(step) : 1 ,pre-Training 손실함수(cost) : 0.421096
Step1 : Mnist 데이터 재구축을 위한 오토인코거 최적화 완료!!
반복(step) : 1 ,pre-Training 손실함수(cost) : 0.420888
Step1 : Mnist 데이터 재구축을 위한 오토인코거 최적화 완료!!
반복(step) :

반복(step) : 1 ,pre-Training 손실함수(cost) : 0.196353
Step1 : Mnist 데이터 재구축을 위한 오토인코거 최적화 완료!!
반복(step) : 1 ,pre-Training 손실함수(cost) : 0.199199
Step1 : Mnist 데이터 재구축을 위한 오토인코거 최적화 완료!!
반복(step) : 1 ,pre-Training 손실함수(cost) : 0.196628
Step1 : Mnist 데이터 재구축을 위한 오토인코거 최적화 완료!!
반복(step) : 1 ,pre-Training 손실함수(cost) : 0.197385
Step1 : Mnist 데이터 재구축을 위한 오토인코거 최적화 완료!!
반복(step) : 1 ,pre-Training 손실함수(cost) : 0.196136
Step1 : Mnist 데이터 재구축을 위한 오토인코거 최적화 완료!!
반복(step) : 1 ,pre-Training 손실함수(cost) : 0.199455
Step1 : Mnist 데이터 재구축을 위한 오토인코거 최적화 완료!!
반복(step) : 1 ,pre-Training 손실함수(cost) : 0.200853
Step1 : Mnist 데이터 재구축을 위한 오토인코거 최적화 완료!!
반복(step) : 1 ,pre-Training 손실함수(cost) : 0.200095
Step1 : Mnist 데이터 재구축을 위한 오토인코거 최적화 완료!!
반복(step) : 1 ,pre-Training 손실함수(cost) : 0.200801
Step1 : Mnist 데이터 재구축을 위한 오토인코거 최적화 완료!!
반복(step) : 1 ,pre-Training 손실함수(cost) : 0.199344
Step1 : Mnist 데이터 재구축을 위한 오토인코거 최적화 완료!!
반복(step) : 1 ,pre-Training 손실함수(cost) : 0.202410
Step1 : Mnist 데이터 재구축을 위한 오토인코거 최적화 완료!!
반복(step) :

반복(step) : 2 ,pre-Training 손실함수(cost) : 0.161251
Step1 : Mnist 데이터 재구축을 위한 오토인코거 최적화 완료!!
반복(step) : 2 ,pre-Training 손실함수(cost) : 0.164411
Step1 : Mnist 데이터 재구축을 위한 오토인코거 최적화 완료!!
반복(step) : 2 ,pre-Training 손실함수(cost) : 0.162157
Step1 : Mnist 데이터 재구축을 위한 오토인코거 최적화 완료!!
반복(step) : 2 ,pre-Training 손실함수(cost) : 0.164595
Step1 : Mnist 데이터 재구축을 위한 오토인코거 최적화 완료!!
반복(step) : 2 ,pre-Training 손실함수(cost) : 0.163884
Step1 : Mnist 데이터 재구축을 위한 오토인코거 최적화 완료!!
반복(step) : 2 ,pre-Training 손실함수(cost) : 0.160507
Step1 : Mnist 데이터 재구축을 위한 오토인코거 최적화 완료!!
반복(step) : 2 ,pre-Training 손실함수(cost) : 0.165827
Step1 : Mnist 데이터 재구축을 위한 오토인코거 최적화 완료!!
반복(step) : 2 ,pre-Training 손실함수(cost) : 0.162377
Step1 : Mnist 데이터 재구축을 위한 오토인코거 최적화 완료!!
반복(step) : 2 ,pre-Training 손실함수(cost) : 0.163028
Step1 : Mnist 데이터 재구축을 위한 오토인코거 최적화 완료!!
반복(step) : 2 ,pre-Training 손실함수(cost) : 0.163449
Step1 : Mnist 데이터 재구축을 위한 오토인코거 최적화 완료!!
반복(step) : 2 ,pre-Training 손실함수(cost) : 0.164100
Step1 : Mnist 데이터 재구축을 위한 오토인코거 최적화 완료!!
반복(step) :

반복(step) : 2 ,pre-Training 손실함수(cost) : 0.164042
Step1 : Mnist 데이터 재구축을 위한 오토인코거 최적화 완료!!
반복(step) : 2 ,pre-Training 손실함수(cost) : 0.165670
Step1 : Mnist 데이터 재구축을 위한 오토인코거 최적화 완료!!
반복(step) : 2 ,pre-Training 손실함수(cost) : 0.167237
Step1 : Mnist 데이터 재구축을 위한 오토인코거 최적화 완료!!
반복(step) : 2 ,pre-Training 손실함수(cost) : 0.166433
Step1 : Mnist 데이터 재구축을 위한 오토인코거 최적화 완료!!
반복(step) : 2 ,pre-Training 손실함수(cost) : 0.162523
Step1 : Mnist 데이터 재구축을 위한 오토인코거 최적화 완료!!
반복(step) : 2 ,pre-Training 손실함수(cost) : 0.165858
Step1 : Mnist 데이터 재구축을 위한 오토인코거 최적화 완료!!
반복(step) : 2 ,pre-Training 손실함수(cost) : 0.167520
Step1 : Mnist 데이터 재구축을 위한 오토인코거 최적화 완료!!
반복(step) : 2 ,pre-Training 손실함수(cost) : 0.165261
Step1 : Mnist 데이터 재구축을 위한 오토인코거 최적화 완료!!
반복(step) : 2 ,pre-Training 손실함수(cost) : 0.167620
Step1 : Mnist 데이터 재구축을 위한 오토인코거 최적화 완료!!
반복(step) : 2 ,pre-Training 손실함수(cost) : 0.166120
Step1 : Mnist 데이터 재구축을 위한 오토인코거 최적화 완료!!
반복(step) : 2 ,pre-Training 손실함수(cost) : 0.164766
Step1 : Mnist 데이터 재구축을 위한 오토인코거 최적화 완료!!
반복(step) :

반복(step) : 3 ,pre-Training 손실함수(cost) : 0.165270
Step1 : Mnist 데이터 재구축을 위한 오토인코거 최적화 완료!!
반복(step) : 3 ,pre-Training 손실함수(cost) : 0.164213
Step1 : Mnist 데이터 재구축을 위한 오토인코거 최적화 완료!!
반복(step) : 3 ,pre-Training 손실함수(cost) : 0.166693
Step1 : Mnist 데이터 재구축을 위한 오토인코거 최적화 완료!!
반복(step) : 3 ,pre-Training 손실함수(cost) : 0.168281
Step1 : Mnist 데이터 재구축을 위한 오토인코거 최적화 완료!!
반복(step) : 3 ,pre-Training 손실함수(cost) : 0.166561
Step1 : Mnist 데이터 재구축을 위한 오토인코거 최적화 완료!!
반복(step) : 3 ,pre-Training 손실함수(cost) : 0.166850
Step1 : Mnist 데이터 재구축을 위한 오토인코거 최적화 완료!!
반복(step) : 3 ,pre-Training 손실함수(cost) : 0.165587
Step1 : Mnist 데이터 재구축을 위한 오토인코거 최적화 완료!!
반복(step) : 3 ,pre-Training 손실함수(cost) : 0.166265
Step1 : Mnist 데이터 재구축을 위한 오토인코거 최적화 완료!!
반복(step) : 3 ,pre-Training 손실함수(cost) : 0.166549
Step1 : Mnist 데이터 재구축을 위한 오토인코거 최적화 완료!!
반복(step) : 3 ,pre-Training 손실함수(cost) : 0.167347
Step1 : Mnist 데이터 재구축을 위한 오토인코거 최적화 완료!!
반복(step) : 3 ,pre-Training 손실함수(cost) : 0.167965
Step1 : Mnist 데이터 재구축을 위한 오토인코거 최적화 완료!!
반복(step) :

...

반복(step) : 16 ,pre-Training 손실함수(cost) : 2.302585
Step2 : Mnist 데이터 재구축을 위한 오토인코거 최적화 완료 + softmax 분류기 최적화 완료(Fine Tuning)!!
반복(step) : 16 ,pre-Training 손실함수(cost) : 2.302585
Step2 : Mnist 데이터 재구축을 위한 오토인코거 최적화 완료 + softmax 분류기 최적화 완료(Fine Tuning)!!
반복(step) : 16 ,pre-Training 손실함수(cost) : 2.302585
Step2 : Mnist 데이터 재구축을 위한 오토인코거 최적화 완료 + softmax 분류기 최적화 완료(Fine Tuning)!!
반복(step) : 16 ,pre-Training 손실함수(cost) : 2.302585
Step2 : Mnist 데이터 재구축을 위한 오토인코거 최적화 완료 + softmax 분류기 최적화 완료(Fine Tuning)!!
반복(step) : 16 ,pre-Training 손실함수(cost) : 2.302585
Step2 : Mnist 데이터 재구축을 위한 오토인코거 최적화 완료 + softmax 분류기 최적화 완료(Fine Tuning)!!
반복(step) : 16 ,pre-Training 손실함수(cost) : 2.302585
Step2 : Mnist 데이터 재구축을 위한 오토인코거 최적화 완료 + softmax 분류기 최적화 완료(Fine Tuning)!!
반복(step) : 16 ,pre-Training 손실함수(cost) : 2.302585
Step2 : Mnist 데이터 재구축을 위한 오토인코거 최적화 완료 + softmax 분류기 최적화 완료(Fine Tuning)!!
반복(step) : 16 ,pre-Training 손실함수(cost) : 2.302585
Step2 : Mnist 데이터 재구축을 위한 오토인코거 최적화 완료 + softmax 분류기 최적화 완료(Fine Tuning)!!


반복(step) : 16 ,pre-Training 손실함수(cost) : 2.302585
Step2 : Mnist 데이터 재구축을 위한 오토인코거 최적화 완료 + softmax 분류기 최적화 완료(Fine Tuning)!!
반복(step) : 16 ,pre-Training 손실함수(cost) : 2.302585
Step2 : Mnist 데이터 재구축을 위한 오토인코거 최적화 완료 + softmax 분류기 최적화 완료(Fine Tuning)!!
반복(step) : 16 ,pre-Training 손실함수(cost) : 2.302585
Step2 : Mnist 데이터 재구축을 위한 오토인코거 최적화 완료 + softmax 분류기 최적화 완료(Fine Tuning)!!
반복(step) : 16 ,pre-Training 손실함수(cost) : 2.302585
Step2 : Mnist 데이터 재구축을 위한 오토인코거 최적화 완료 + softmax 분류기 최적화 완료(Fine Tuning)!!
반복(step) : 16 ,pre-Training 손실함수(cost) : 2.302585
Step2 : Mnist 데이터 재구축을 위한 오토인코거 최적화 완료 + softmax 분류기 최적화 완료(Fine Tuning)!!
반복(step) : 16 ,pre-Training 손실함수(cost) : 2.302585
Step2 : Mnist 데이터 재구축을 위한 오토인코거 최적화 완료 + softmax 분류기 최적화 완료(Fine Tuning)!!
반복(step) : 16 ,pre-Training 손실함수(cost) : 2.302585
Step2 : Mnist 데이터 재구축을 위한 오토인코거 최적화 완료 + softmax 분류기 최적화 완료(Fine Tuning)!!
반복(step) : 16 ,pre-Training 손실함수(cost) : 2.302585
Step2 : Mnist 데이터 재구축을 위한 오토인코거 최적화 완료 + softmax 분류기 최적화 완료(Fine Tuning)!!


반복(step) : 17 ,pre-Training 손실함수(cost) : 2.302585
Step2 : Mnist 데이터 재구축을 위한 오토인코거 최적화 완료 + softmax 분류기 최적화 완료(Fine Tuning)!!
반복(step) : 17 ,pre-Training 손실함수(cost) : 2.302585
Step2 : Mnist 데이터 재구축을 위한 오토인코거 최적화 완료 + softmax 분류기 최적화 완료(Fine Tuning)!!
반복(step) : 17 ,pre-Training 손실함수(cost) : 2.302585
Step2 : Mnist 데이터 재구축을 위한 오토인코거 최적화 완료 + softmax 분류기 최적화 완료(Fine Tuning)!!
반복(step) : 17 ,pre-Training 손실함수(cost) : 2.302585
Step2 : Mnist 데이터 재구축을 위한 오토인코거 최적화 완료 + softmax 분류기 최적화 완료(Fine Tuning)!!
반복(step) : 17 ,pre-Training 손실함수(cost) : 2.302585
Step2 : Mnist 데이터 재구축을 위한 오토인코거 최적화 완료 + softmax 분류기 최적화 완료(Fine Tuning)!!
반복(step) : 17 ,pre-Training 손실함수(cost) : 2.302585
Step2 : Mnist 데이터 재구축을 위한 오토인코거 최적화 완료 + softmax 분류기 최적화 완료(Fine Tuning)!!
반복(step) : 17 ,pre-Training 손실함수(cost) : 2.302585
Step2 : Mnist 데이터 재구축을 위한 오토인코거 최적화 완료 + softmax 분류기 최적화 완료(Fine Tuning)!!
반복(step) : 17 ,pre-Training 손실함수(cost) : 2.302585
Step2 : Mnist 데이터 재구축을 위한 오토인코거 최적화 완료 + softmax 분류기 최적화 완료(Fine Tuning)!!


반복(step) : 17 ,pre-Training 손실함수(cost) : 2.302585
Step2 : Mnist 데이터 재구축을 위한 오토인코거 최적화 완료 + softmax 분류기 최적화 완료(Fine Tuning)!!
반복(step) : 17 ,pre-Training 손실함수(cost) : 2.302585
Step2 : Mnist 데이터 재구축을 위한 오토인코거 최적화 완료 + softmax 분류기 최적화 완료(Fine Tuning)!!
반복(step) : 17 ,pre-Training 손실함수(cost) : 2.302585
Step2 : Mnist 데이터 재구축을 위한 오토인코거 최적화 완료 + softmax 분류기 최적화 완료(Fine Tuning)!!
반복(step) : 17 ,pre-Training 손실함수(cost) : 2.302585
Step2 : Mnist 데이터 재구축을 위한 오토인코거 최적화 완료 + softmax 분류기 최적화 완료(Fine Tuning)!!
반복(step) : 17 ,pre-Training 손실함수(cost) : 2.302585
Step2 : Mnist 데이터 재구축을 위한 오토인코거 최적화 완료 + softmax 분류기 최적화 완료(Fine Tuning)!!
반복(step) : 17 ,pre-Training 손실함수(cost) : 2.302585
Step2 : Mnist 데이터 재구축을 위한 오토인코거 최적화 완료 + softmax 분류기 최적화 완료(Fine Tuning)!!
반복(step) : 17 ,pre-Training 손실함수(cost) : 2.302585
Step2 : Mnist 데이터 재구축을 위한 오토인코거 최적화 완료 + softmax 분류기 최적화 완료(Fine Tuning)!!
반복(step) : 17 ,pre-Training 손실함수(cost) : 2.302585
Step2 : Mnist 데이터 재구축을 위한 오토인코거 최적화 완료 + softmax 분류기 최적화 완료(Fine Tuning)!!


반복(step) : 18 ,pre-Training 손실함수(cost) : 2.302585
Step2 : Mnist 데이터 재구축을 위한 오토인코거 최적화 완료 + softmax 분류기 최적화 완료(Fine Tuning)!!
반복(step) : 18 ,pre-Training 손실함수(cost) : 2.302585
Step2 : Mnist 데이터 재구축을 위한 오토인코거 최적화 완료 + softmax 분류기 최적화 완료(Fine Tuning)!!
반복(step) : 18 ,pre-Training 손실함수(cost) : 2.302585
Step2 : Mnist 데이터 재구축을 위한 오토인코거 최적화 완료 + softmax 분류기 최적화 완료(Fine Tuning)!!
반복(step) : 18 ,pre-Training 손실함수(cost) : 2.302585
Step2 : Mnist 데이터 재구축을 위한 오토인코거 최적화 완료 + softmax 분류기 최적화 완료(Fine Tuning)!!
반복(step) : 18 ,pre-Training 손실함수(cost) : 2.302585
Step2 : Mnist 데이터 재구축을 위한 오토인코거 최적화 완료 + softmax 분류기 최적화 완료(Fine Tuning)!!
반복(step) : 18 ,pre-Training 손실함수(cost) : 2.302585
Step2 : Mnist 데이터 재구축을 위한 오토인코거 최적화 완료 + softmax 분류기 최적화 완료(Fine Tuning)!!
반복(step) : 18 ,pre-Training 손실함수(cost) : 2.302585
Step2 : Mnist 데이터 재구축을 위한 오토인코거 최적화 완료 + softmax 분류기 최적화 완료(Fine Tuning)!!
반복(step) : 18 ,pre-Training 손실함수(cost) : 2.302585
Step2 : Mnist 데이터 재구축을 위한 오토인코거 최적화 완료 + softmax 분류기 최적화 완료(Fine Tuning)!!
